In [1]:
%load_ext autoreload
%autoreload
%cd /home/jupyter/MathVGerrmandering_CMAT_2021/
from src import *
from src.data import *
from src.space import *
from src.mcmc import *

# https://dvr.capitol.texas.gov/
level    = 'cntyvtd'
proposal = 'plans2168'  # for 2010 enacted, use 'planc2100' for US congress, 'plans2100' for TX Senate, or 'planh2100' for TX House
contract = 0
# contract = 'proposal'

# D = Data()
S = Space(level=level, proposal=proposal, contract=contract)
M = MCMC(gpickle=S.gpickle, nodes=S.tbls['nodes'],
         max_steps   = 5,
         random_seed = 13,
         defect_cap  = 100,
         pop_deviation_target=10)
# M.run_chain()
# M.post_process()

/home/jupyter/MathVGerrmandering_CMAT_2021
getting states
Get proposal    ... using existing table ... success!
Get nodes       ... using existing table ... success!
Get graph       ... processing ... using existing graph ... success!


In [2]:
try:
    import pandas_bokeh
except:
    os.system('pip install --upgrade pandas-bokeh')
    import pandas_bokeh
pandas_bokeh.output_notebook()

plan_cols = ['geoid', 'plan', 'district']
query = f"select {', '.join(plan_cols)} from {M.output}"
plans = run_query(query).pivot(index='geoid', columns='plan', values='district')
repl = {c:str(c) for c in plans.columns}
plans.rename(columns=repl, inplace=True)

node_cols = ['geoid', 'polygon', 'county', 'total_pop', 'aland', 'density', 'polsby_popper']
query = f"select {', '.join(node_cols)} from {M.nodes}"
nodes = run_query(query).set_index('geoid')
geo = gpd.GeoSeries.from_wkt(nodes['polygon'], crs=crs_census).simplify(0.003).buffer(0) #<-- little white space @ .001 ~5.7 mb, minimal at .0001 ~10mb, with no white space ~37mb

Loading BokehJS ...

In [5]:
recolor = dict(zip(M.districts, M.rng.permutation(M.districts)))
gdf = gpd.GeoDataFrame(nodes
                       .drop(columns='polygon')
                       .join(plans.replace(recolor), how='inner')
                       , geometry=geo).reset_index()

In [7]:
width = 600
xlim = [-106.2, -94.0]
ylim = [ 25.4 ,  36.6]
aspect = (ylim[1] - ylim[0]) / (xlim[1] - xlim[0])
height = round(aspect * width)

def f(cmap):
    fn = str(M.gpickle)
    fn = f'{fn[:fn.rfind("_")]}_{M.random_seed}_animation_{cmap}.html'
    print(f'cmap={cmap} ... saving animation to {fn}')
    fig = gdf.plot_bokeh(
        colormap = cmap,
        hovertool_string = '@geoid, @county<br>pop=@total_pop<br>density=@density{0.0}<br>land=@aland{0.0}<br>pp=@polsby_popper{0.0}',
        fill_alpha = 0.5,
        line_alpha = 0.05,
        return_html = True,
        show_figure = True,
        slider = list(repl.values()),
        slider_name = "PLAN",
        show_colorbar = False,
        xlim = xlim,
        ylim = ylim,
        figsize = (width, height),
    )
    with open(fn, 'w') as file:
        file.write(fig)
    return fig

f('Paired')

# for cmap in ['Accent', 'Blues', 'Bokeh', 'BrBG', 'BuGn', 'BuPu', 'Category10', 'Category20', 'Category20b', 'Category20c',
#              'Cividis', 'Colorblind', 'Dark2', 'GnBu', 'Greens', 'Greys', 'Inferno', 'Magma', 'OrRd', 'Oranges', 'PRGn',
#              'Paired', 'Pastel1', 'Pastel2', 'PiYG', 'Plasma', 'PuBu', 'PuBuGn', 'PuOr', 'PuRd', 'Purples', 'RdBu', 'RdGy',
#              'RdPu', 'RdYlBu', 'RdYlGn', 'Reds', 'Set1', 'Set2', 'Set3', 'Spectral', 'Turbo', 'Viridis', 'YlGn', 'YlGnBu',
#              'YlOrBr', 'YlOrRd']:
#     f(cmap)

cmap=Paired ... saving animation to /home/jupyter/redistricting_data/proposals/TX/sldu/plans2168/TX_sldu_plans2168_cntyvtd_0_13_animation_Paired.html


/opt/conda/lib/python3.7/site-packages/pandas_bokeh/geoplot.py:118: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for polygon in geometry:


'<script src="https://cdn.bokeh.org/bokeh/release/bokeh-2.4.1.min.js"></script>\n<script src="https://cdn.bokeh.org/bokeh/release/bokeh-gl-2.4.1.min.js"></script>\n<script src="https://cdn.bokeh.org/bokeh/release/bokeh-widgets-2.4.1.min.js"></script>\n<script src="https://cdn.bokeh.org/bokeh/release/bokeh-tables-2.4.1.min.js"></script>\n<script src="https://cdn.bokeh.org/bokeh/release/bokeh-mathjax-2.4.1.min.js"></script>\n\n\n\n<div class="bk-root" id="bf00d15f-5088-4af0-b137-945f803f3fa5" data-root-id="1473"></div>\n\n\n<script type="text/javascript">\n    (function() {\n          const fn = function() {\n            Bokeh.safely(function() {\n              (function(root) {\n                function embed_document(root) {\n                  \n                const docs_json = \'{"8da70b0b-8883-45e2-8aeb-93924b908757":{"defs":[],"roots":{"references":[{"attributes":{"children":[{"id":"1471"},{"id":"1401"}]},"id":"1473","type":"Column"},{"attributes":{"zoom_on_axis":false},"id":"1429"